In [1]:
import pandas as pd
from prophet import Prophet
# from neuralprophet import NeuralProphet# as Prophet
# from neuralprophet import set_log_level
# set_log_level("ERROR")

from dotenv import load_dotenv
from pathlib import Path
import os

# from ezekial.prophet import Prophet
import yfinance as yf
import requests
import base64
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
from tqdm.auto import tqdm
from multiprocessing import Pool, cpu_count, Process#, freeze_support
import time
import warnings
import sys

In [2]:
# Arguements
warnings.filterwarnings("ignore")
load_dotenv()
url = os.getenv("DJANGO_SERVER_URL")
av_key = os.getenv("APLHA_VANTAGE_KEY")
av_key1 = os.getenv("APLHA_VANTAGE_KEY1")
av_key2 = os.getenv("APLHA_VANTAGE_KEY2")
av_key3 = os.getenv("APLHA_VANTAGE_KEY3")
av_key4 = os.getenv("APLHA_VANTAGE_KEY4")
av_key5 = os.getenv("APLHA_VANTAGE_KEY5")
av_key6 = os.getenv("APLHA_VANTAGE_KEY6")
ma_key = os.getenv("MARKETAUX_TOKEN")
ma_key1 = os.getenv("MARKETAUX_TOKEN2")
ma_key2 = os.getenv("MARKETAUX_TOKEN3")
ma_key3 = os.getenv("MARKETAUX_TOKEN4")
ma_key4 = os.getenv("MARKETAUX_TOKEN5")

weeeks_prior_data_end_date = int(sys.argv[1]) #260
forecast_days_ahead = int(sys.argv[2]) #90
ticker_path = sys.argv[3]#'data/S&P500 tickers.csv'
forecast_img_path = sys.argv[4]#'images/forecast_temp/forecast.png'

In [3]:
# # Arguements
# warnings.filterwarnings("ignore")
# load_dotenv()
# url = os.getenv("DJANGO_SERVER_URL")
# url = os.getenv("DJANGO_SERVER_URL")
# av_key = os.getenv("APLHA_VANTAGE_KEY")
# av_key1 = os.getenv("APLHA_VANTAGE_KEY1")
# av_key2 = os.getenv("APLHA_VANTAGE_KEY2")
# av_key3 = os.getenv("APLHA_VANTAGE_KEY3")
# av_key4 = os.getenv("APLHA_VANTAGE_KEY4")
# av_key5 = os.getenv("APLHA_VANTAGE_KEY5")
# av_key6 = os.getenv("APLHA_VANTAGE_KEY6")
# ma_key = os.getenv("MARKETAUX_TOKEN")
# ma_key1 = os.getenv("MARKETAUX_TOKEN2")
# ma_key2 = os.getenv("MARKETAUX_TOKEN3")
# ma_key3 = os.getenv("MARKETAUX_TOKEN4")
# ma_key4 = os.getenv("MARKETAUX_TOKEN5")

# weeeks_prior_data_end_date = 12
# forecast_days_ahead = 90
# ticker_path = 'data/S&P500 tickers.csv'
# forecast_img_path = 'images/forecast_temp/forecast.png'

In [4]:
# print(weeeks_prior_data_end_date)
# print(forecast_days_ahead)
# print(ticker_path)
# print(forecast_img_path)

In [5]:
def load_tickers(ticker_path):
    """
    Takes five hundred tickers, which is max calls of yfinance for public ip.
    """
    ticker_file_path = Path(ticker_path)
    ticker_df = pd.read_csv(ticker_file_path)
    prophet_ticker_list = ticker_df['Symbol'].head(500).to_list()
    return prophet_ticker_list

def django_get(url):
    response = requests.get(url)
    response_json = response.json()
    return response_json

def clear_django_sql_db(url):
    """
    Clears the sql db in the django api.
    "DJANGO_SERVER_URL" is provided in .env file.
    """

    try:
        # load_dotenv()
        # url = os.getenv("DJANGO_SERVER_URL")

        django_api_items = django_get(url)

        if len(django_api_items) != 0:
            for x, index_id in enumerate(django_api_items):
                x += 1
                str_indx = str(index_id['id'])

                if x == 1:
                    url += str(str_indx)
                    requests.delete(url)
                    # print(f'entered if block\t{url}')
                else:
                    try:
                        url = url[:-len(str_indx)] + str_indx
                        requests.delete(url)
                        # print(f'entered else block\t{url}')
                    # For when the number of digits change
                    except:
                        url = url[:-len(str_indx) + 1] + str_indx
                        requests.delete(url)                    
                        # print(f'entered else block\t{url}')
            print(f"Django SQL DB cleared:\n\n{django_get(url)}")
        else:
            print(f"Django SQL DB Already empty:\n\n{django_get(url)}")
    except:
        print(f"Django server did not clear:\n\n{django_get(url)}")

def run_prophet(timeserie, forecast_ahead = forecast_days_ahead):
    model = Prophet(interval_width=0.95, changepoint_range=0.75, changepoint_prior_scale=0.05)
    # model = Prophet(yearly_seasonality=False,daily_seasonality=False)
    model.fit(timeserie)
    forecast = model.make_future_dataframe(periods=forecast_ahead, include_history=True)
    forecast = model.predict(forecast)
    return forecast

# def make_plots(predictions, url = url):
# # def make_plots(predictions, series, adj_close_df, url = url):
#     # Attempt to clear the SQL DB if it fails initially before uploading the data again, 
#     # to reduce DB size for POST request on the APP side
#     try: clear_django_sql_db(url = url)
#     except: 
#         try: clear_django_sql_db(url = url)
#         except: error_msg = '\t##### Could not clear the Django SQL DB  #####'

#     for idx, fig_plot in enumerate(predictions):
#         forecast_plot = pd.merge(left=fig_plot, right=series[idx], on='ds', how='outer')
#         ticker_sym = adj_close_df.columns[idx]
#         forecast_plot = forecast_plot[-(forecast_days_ahead - 10) - 30:-(forecast_days_ahead - 10)]
#         forecast_plot.index = forecast_plot['ds']

#         with plt.style.context('dark_background'):
#             fig, ax = plt.subplots()
#             forecast_plot[['y','yhat']].plot(ax=ax, figsize = (8,10), style=['o-','--'],color=['r','lightblue'],linewidth=1)
#             ax.set_xlabel('Date', fontdict={'size':12})
#             ax.set_ylabel('Price', fontdict={'size':12})
#             ax.yaxis.set_major_formatter('${x:,.0f}')
#             ax.legend(['Actual','Forecasted'], title= f'{ticker_sym}', loc='upper center', frameon=False)
#             # ax.set_facecolor('xkcd:black')
#         # plt.show()
#         try:
#             fig.savefig(forecast_img_path)
#             with open(forecast_img_path, "rb") as image2string:
#                 converted_string = base64.b64encode(image2string.read())
#             image2string.close()

#             json_post = {
#                 "ticker": f"{ticker_sym}",
#                 "time": f'{today}'[:15],
#                 "encoded_string": f"{converted_string}"
#             }

#             try:
#                 requests.post(url,json_post)
#                 print(f"+++ {ticker_sym} success!")
#             except:
#                 print(f"\t--- {ticker_sym} failed ---")
#         except:
#             print(f"\t---# {ticker_sym} failed #---")
#             print("\n\n\tyfinance API daily limit reached.")

def make_plots(prediction, seri, adj_cl, idx):

    forecast_plot = pd.merge(left=prediction, right=seri, on='ds', how='outer')
    ticker_sym = adj_cl
    
    if idx < 100:
        ma_key_valu = ma_key
    elif idx < 200:
        ma_key_valu = ma_key1
    elif idx < 300:
        ma_key_valu = ma_key2
    elif idx < 400:
        ma_key_valu = ma_key3
    else:
        ma_key_valu = ma_key4
        
    ######
    try:
        ma_url = f'https://api.marketaux.com/v1/news/all?symbols={ticker_sym}&filter_entities=true&group_similar=false&language=en&api_token={ma_key_valu}'
        setntiment_data = requests.get(ma_url).json()

        mean_score = 0
        for i in range(len(setntiment_data['data'])):
            mean_score += setntiment_data['data'][i]['entities'][0]['sentiment_score']

        mean_score /= len(setntiment_data['data'])
    except:
        mean_score = 'NULL'
    
    
    # # def weather_emoticons(i):
    # """
    # Returns the percent change for the first 10 forecasted values,
    # taking the dot product of 1000 and casting it as an int.
    # Outliers are automatically converted to max values of the
    # ordinal scale, (-5, 5).
    # """
    # # forecast_plot = pd.merge(left=prediction, right=seri, on='ds', how='outer')
    # forecast_plot.index = forecast_plot['ds']
    # def correct_max_outliers (z):     
    #     if z > 5: z = 5
    #     elif z < -5: z = -5
    #     return z
    # weather_df = forecast_plot[['yhat']].pct_change()[-forecast_days_ahead:-(forecast_days_ahead - 10)].dot([1000]).astype(int).apply(correct_max_outliers)
    # # return weather_df
    # weather_df = [[str(x)[-22:] for x in weather_df.index], [y for y in weather_df]]

    ########################################################################
    ## ENCODE QUANTILES FOR FORECASTS USING PCT_CHANGE OF HISTORICAL DATA ##
    ########################################################################
    forecast_plot.index = forecast_plot['ds']
    # forecast_pct_change = forecast_plot[['yhat1']].pct_change().dropna().dot([1000]).astype(int)
    # forecast_pct_change = forecast_plot[['y']].dropna().pct_change().dropna().dot([1000]).astype(int)
    yhat_descriptive_stats = forecast_plot[['y']].dropna().pct_change().dropna().dot([1000]).astype(int).describe()

    twentyfive_percent = float(yhat_descriptive_stats.iloc[4])
    fifty_percent = float(yhat_descriptive_stats.iloc[5])
    seventy_five_percent = float(yhat_descriptive_stats.iloc[6])

    def encode_quantiles (z):     
        if z < twentyfive_percent: z = 0
        elif z < fifty_percent: z = 1
        elif z < seventy_five_percent: z = 3
        else: z = 4
        return z

    weather_df = forecast_plot[['yhat']].pct_change().dropna().dot([1000]).astype(int)[-forecast_days_ahead:-(forecast_days_ahead - 10)].apply(encode_quantiles)
    weather_df = [[str(x)[-22:] for x in weather_df.index], [y for y in weather_df]]

    

    forecast_plot = forecast_plot[-(forecast_days_ahead - 10) - 30:-(forecast_days_ahead - 10)]
    # forecast_plot.index = forecast_plot['ds']

    with plt.style.context('dark_background'):
        fig, ax = plt.subplots()
        forecast_plot[['y','yhat']].plot(ax=ax, figsize = (8,10), style=['o-','--'],color=['r','lightblue'],linewidth=1)
        ax.set_xlabel('Date', fontdict={'size':12})
        ax.set_ylabel('Price', fontdict={'size':12})
        ax.yaxis.set_major_formatter('${x:,.0f}')
        ax.legend(['Actual','Forecasted'], title= f'{ticker_sym}', loc='upper center', frameon=False)
        # ax.set_facecolor('xkcd:black')
    # plt.show()
    try:
        # new_forecast_img_path = forecast_img_path + F'_{ticker_sym}.png'
        fig.savefig(forecast_img_path)
        with open(forecast_img_path, "rb") as image2string:
            converted_string = base64.b64encode(image2string.read())
        image2string.close()

        # JSON TO BE POSTED TO API
        json_post = {
            "ticker": f"{ticker_sym}",
            "time": f'{today}'[:16],
            "encoded_string": f"{converted_string}",
            "emoticons": f"{weather_df}",
            "sentiment": f"{mean_score}"
        }

        try:
            requests.post(url,json_post)
            print(f"+++ {ticker_sym} success!")
        except:
            print(f"\t--- {ticker_sym} failed ---")
    except:
        print(f"\t---# {ticker_sym} failed #---")
        print("\n\n\tyfinance API daily limit reached.")

In [125]:
# first_key = [(ma_key, i) for i in adj_close_df.columns[:100]]
# second_key = [(ma_key1, j) for j in adj_close_df.columns[200:300]]
# third_key = [(ma_key2, k) for k in adj_close_df.columns[200:300]]
# fourth_key = [(ma_key3, l) for l in adj_close_df.columns[200:300]]
# fifth_key = [(ma_key4, m) for m in adj_close_df.columns[200:300]]

# for i in second_key:
#     first_key.append(i)
# for i in third_key:
#     first_key.append(i)
# for i in fourth_key:
#     first_key.append(i)
# for i in fifth_key:
#     first_key.append(i)

# def calc_mean_score(ma_key_value, ticker_name_sym):
#     """
#     Accepts marketaux api key:
#       https://www.marketaux.com/documentation
#     Also accepts a ticker symbol.
    
#     Returns tickers mean sentiment score for time nearest calling the func.
#     """
#     ma_url = f'https://api.marketaux.com/v1/news/all?symbols={ticker_name_sym}&filter_entities=true&group_similar=false&language=en&api_token={ma_key_value}'
#     setntiment_data = requests.get(ma_url).json()
    
#     mean_score = 0
#     for i in range(len(setntiment_data['data'])):
#         mean_score += setntiment_data['data'][i]['entities'][0]['sentiment_score']

#     mean_score /= len(setntiment_data['data'])
    
#     return mean_score
#     # return ticker_name_sym, mean_score
    
# sentiment_series = pd.Series()
# empty_sentiment_series = pd.Series('NULL')

# for n in first_key[498:]:
#     try: sentiment_series = pd.concat([sentiment_series, pd.Series(calc_mean_score(n[0], n[1]))])
#     except: sentiment_series.concat([sentiment_series, empty_sentiment_series])

In [6]:
# weather_df = forecast_plot[['yhat']].pct_change()[-forecast_days_ahead:-(forecast_days_ahead - 10)].dot([1000]).astype(int).apply(correct_max_outliers)

# this_index = [[str(x)[-22:] for x in weather_df.index], [y for y in weather_df]]
# this_index

In [7]:
# start_time = time.time()
# today = datetime.today()
# start_date = today - timedelta(weeks=weeeks_prior_data_end_date)
# start_date = start_date.replace(second=0, microsecond=0)

# data = yf.download(load_tickers(ticker_path), start=start_date)
# adj_close_df = data['Adj Close']
# adj_close_df = adj_close_df.dropna(axis=1, how='all')
# series = [adj_close_df[f'{col}'].reset_index().rename({'Date':'ds', f'{col}':'y'}, axis=1) for col in adj_close_df]

# start_time0 = time.time()
# p = Pool(cpu_count())
# predictions = list(tqdm(p.imap(run_prophet, series), total=len(series)))
# p.close()
# p.join()
# print("--- %s seconds ---" % (time.time() - start_time0))

# # make_plots(url)

# # try: print(error_msg)
# # except: print("\t+++++ The SQL DB was successfully cleared +++++")

# # print("--- %s seconds ---" % (time.time() - start_time))

In [8]:
start_time = time.time()
today = datetime.today()
start_date = today - timedelta(weeks=weeeks_prior_data_end_date)
start_date = start_date.replace(second=0, microsecond=0)

data = yf.download(load_tickers(ticker_path), start=start_date)
adj_close_df = data['Adj Close']
adj_close_df = adj_close_df.dropna(axis=1, how='all')
series = [adj_close_df[f'{col}'].reset_index().rename({'Date':'ds', f'{col}':'y'}, axis=1) for col in adj_close_df]


start_time00 = time.time()
p1 = Pool(cpu_count())
predictions1 = list(tqdm(p1.imap(run_prophet, series), total=len(series)))
p1.close()
p1.join()
print("--- %s seconds ---" % (time.time() - start_time00))

[*********************100%***********************]  500 of 500 completed

2 Failed downloads:
- BRK.B: No data found, symbol may be delisted
- BF.B: No data found for this date range, symbol may be delisted


  0%|          | 0/498 [00:00<?, ?it/s]

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to overr


Initial log joint probability = -23.5306
Iteration  1. Log joint probability =    67.9814. Improved by 91.512.

Initial log joint probability = -23.2931

Iteration  1. Log joint probability =    106.849. Improved by 130.142.

Initial log joint probability = -23.3548
Iteration  2. Log joint probability =    112.557. Improved by 44.5758.
Initial log joint probability = -23.2836
Iteration  2. Log joint probability =    143.322. Improved by 36.4734.
Iteration  3. Log joint probability =    126.428. Improved by 13.8712.
Iteration  1. Log joint probability =    97.6719. Improved by 121.027.
Iteration  1. Log joint probability =    192.871. Improved by 216.155.
Iteration  4. Log joint probability =    126.741. Improved by 0.312923.

Initial log joint probability = -23.3184
Iteration  2. Log joint probability =    133.687. Improved by 36.0155.
Iteration  3. Log joint probability =    153.622. Improved by 10.2998.
Iteration  5. Log joint probability =    126.745. Improved by 0.003756.
Iteratio

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to overr

...

Iteration 52. Log joint probability =    186.475. Improved by 0.00206964.
Iteration 53. Log joint probability =    186.476. Improved by 0.00137945.
Iteration 54. Log joint probability =    186.478. Improved by 0.00183395.
Iteration 55. Log joint probability =    186.478. Improved by 0.000297582.
Iteration 56. Log joint probability =    186.479. Improved by 0.00107238.
Iteration 57. Log joint probability =     186.48. Improved by 0.000470731.
Iteration 58. Log joint probability =     186.48. Improved by 0.000221687.
Iteration 59. Log joint probability =    186.481. Improved by 0.001053.
Iteration 60. Log joint probability =    186.482. Improved by 0.000541772.
Iteration 61. Log joint probability =    186.482. Improved by 0.000275313.
Iteration 62. Log joint probability =    186.482. Improved by 0.000411759.
Iteration 63. Log joint probability =    186.483. Improved by 0.000228499.
Iteration 64. Log joint probability =    186.483. Improved by 0.000205359.
Iteration 65. Log joint probabil

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.



Initial log joint probability = -23.3132
Iteration  1. Log joint probability =    103.892. Improved by 127.205.
Iteration 80. Log joint probability =    186.483. Improved by 2.00881e-06.
Iteration  2. Log joint probability =    140.334. Improved by 36.4422.
Iteration 81. Log joint probability =    186.483. Improved by 1.7843e-06.
Iteration  3. Log joint probability =    175.111. Improved by 34.7772.
Iteration 82. Log joint probability =    186.483. Improved by 5.25612e-06.
Iteration 83. Log joint probability =    186.483. Improved by 1.34674e-06.
Iteration  4. Log joint probability =    195.826. Improved by 20.7151.
Iteration 84. Log joint probability =    186.483. Improved by 2.50462e-06.
Iteration  5. Log joint probability =    198.881. Improved by 3.05498.
Iteration 85. Log joint probability =    186.483. Improved by 3.62539e-08.
Iteration  6. Log joint probability =    198.917. Improved by 0.0359685.
Iteration 86. Log joint probability =    186.483. Improved by 2.29185e-06.
Iterat

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


Iteration 94. Log joint probability =    156.402. Improved by 6.73294e-06.
Iteration 97. Log joint probability =    165.773. Improved by 1.29878e-07.
Iteration 95. Log joint probability =    156.402. Improved by 7.81264e-06.
Iteration 98. Log joint probability =    165.773. Improved by 5.43841e-09.
Iteration 96. Log joint probability =    156.402. Improved by 4.28508e-06.
Iteration 97. Log joint probability =    156.402. Improved by 7.09171e-06.
Iteration 98. Log joint probability =    156.402. Improved by 2.7998e-06.
Iteration 99. Log joint probability =    156.402. Improved by 4.84321e-06.
Iteration 100. Log joint probability =    156.402. Improved by 1.19701e-06.
Iteration 101. Log joint probability =    156.402. Improved by 9.37008e-07.
Iteration 102. Log joint probability =    156.402. Improved by 8.64048e-07.
Iteration 103. Log joint probability =    156.402. Improved by 3.47667e-07.
Iteration 104. Log joint probability =    156.402. Improved by 5.06694e-07.
Iteration 105. Log jo

In [156]:
# first_key = []
# first_key = [(ma_key, i) for i in adj_close_df.columns[:100]]
# second_key = [(ma_key1, j) for j in adj_close_df.columns[200:300]]
# third_key = [(ma_key2, k) for k in adj_close_df.columns[200:300]]
# fourth_key = [(ma_key3, l) for l in adj_close_df.columns[200:300]]
# fifth_key = [(ma_key4, m) for m in adj_close_df.columns[200:300]]

# first_key = []
# first_key = [i for i in adj_close_df.columns[:100]]
# second_key = [j for j in adj_close_df.columns[200:300]]
# third_key = [k for k in adj_close_df.columns[200:300]]
# fourth_key = [l for l in adj_close_df.columns[200:300]]
# fifth_key = [m for m in adj_close_df.columns[200:300]]

# for i in second_key:
#     first_key.append(i)
# for i in third_key:
#     first_key.append(i)
# for i in fourth_key:
#     first_key.append(i)
# for i in fifth_key:
#     first_key.append(i)


In [154]:
# mapping_star = [(predictions1[i], series[i], adj_close_df.columns[i], i) for i in range(len(predictions1))]
# mapping_star0 = [(predictions1[i], series[i], adj_close_df.columns[i], first_key[i]) for i in range(len(predictions1))]
# mapping_star1 = [(predictions1[i], series[i], adj_close_df.columns[i], first_key[i]) for i in range(len(predictions1))]
# mapping_star2 = [(predictions1[i], series[i], adj_close_df.columns[i], first_key[i]) for i in range(len(predictions1))]
# mapping_star3 = [(predictions1[i], series[i], adj_close_df.columns[i], first_key[i]) for i in range(len(predictions1))]

# mapping_star

In [157]:
# mapping_star[0]

In [158]:
# mapping_star = [(predictions1[i], series[i], adj_close_df.columns[i], first_key[i]) for i in range(len(predictions1))]
# mapping_star[0]

In [159]:
# master_mapping_star = []
# for i, j in enumerate(mapping_star):
#     master_mapping_star.append(j, first_key[i])
#     # print(i, j)

In [160]:
# len(mapping_star[0])

In [9]:
# Attempt to clear the SQL DB if it fails initially before uploading the data again, 
# to reduce DB size for POST request on the APP side
try: clear_django_sql_db(url = url)
except: 
    try: clear_django_sql_db(url = url)
    except: error_msg = '\t##### Could not clear the Django SQL DB  #####'

mapping_star = [(predictions1[i], series[i], adj_close_df.columns[i], i) for i in range(len(predictions1))]

start_time1 = time.time()

p = Pool(cpu_count())
p.starmap(make_plots, mapping_star)
p.close()
p.join()
print("--- %s seconds ---" % (time.time() - start_time1))

+++ AES success!
+++ CBRE success!
+++ BKR success!
+++ AFL success!
+++ CCI success!
+++ BLK success!
+++ AIG success!
+++ CCL success!
+++ AMP success!
+++ CDAY success!
+++ AMT success!
+++ BLL success!
+++ CDNS success!
+++ BMY success!
+++ CRL success!
+++ AIZ success!
+++ BR success!
+++ AMZN success!
+++ BRO success!
+++ ANET success!
+++ A success!
+++ BSX success!
+++ AAL success!
+++ CRM success!
+++ CDW success!
+++ ANSS success!
+++ CL success!
+++ AAP success!
+++ ANTM success!
+++ AAPL success!
+++ CSCO success!
+++ ABBV success!
+++ AVGO success!
+++ ABC success!
+++ AJG success!
+++ AVY success!
+++ ABMD success!
+++ AWK success!
+++ CE success!
+++ AXP success!
+++ BWA success!
+++ AZO success!
+++ CLX success!
+++ BA success!
+++ AKAM success!
+++ BAC success!
+++ ALB success!
+++ CMA success!
+++ ALGN success!
+++ BAX success!
+++ ALK success!
+++ CSX success!
+++ AON success!
+++ CTAS success!
+++ AOS success!
+++ CTLT success!
+++ CEG success!
+++ CTRA success!
+++

In [10]:
try: print(error_msg)
except: print("\t+++++ The SQL DB was successfully cleared +++++")

print("--- %s seconds ---" % (time.time() - start_time))

	##### Could not clear the Django SQL DB  #####
--- 405.94898748397827 seconds ---


In [11]:
# p.map(make_plots, predictions)

In [12]:
# clear_django_sql_db(url)

In [13]:
# api_data = django_get(url)#[0]['id']

In [14]:
# len(api_data)

In [15]:
# class save_ticker_image:
#     def __init__(self, url, img_path, ticker):
#         self.url = url
#         self.img_path = img_path
#         self.ticker = ticker
    
#     def django_get(self):
#         response = requests.get(self.url)
#         response_json = response.json()
#         return response_json

#     def select_ticker(self):
#         django_api_dict = self.django_get()
#         for dictionary in django_api_dict:   
#             try:
#                 if dictionary['ticker'] == self.ticker:
#                     encoded_plot = dictionary['encoded_string']
#             except: return print("Ticker Not Found in Forecast Database")
#         # Decode string and save as a .png
#         try:
#             decodeit = open(self.img_path, 'wb')
#             decodeit.write(base64.b64decode(encoded_plot[2:].encode()))
#             decodeit.close()
#             print("Image Saved Successfully")
#         except: return print("Could Not Save Plot Ticker Not Found")

In [16]:
# forecast_decoded_img_path = Path('images/forecast_temp/decoded.png')
# save_ticker_image(url=url, img_path=forecast_decoded_img_path, ticker='AAPL').select_ticker()

In [17]:
# def weather_emoticons(i):
#     """
#     Returns the percent change for the first 10 forecasted values,
#     taking the dot product of 1000 and casting it as an int.
#     Outliers are automatically converted to max values of the
#     ordinal scale, (-5, 5).
#     """
#     forecast_plot = pd.merge(left=mapping_star[i][0], right=mapping_star[i][1], on='ds', how='outer')
#     forecast_plot.index = forecast_plot['ds']
#     def correct_max_outliers (z):     
#         if z > 5: z = 5
#         elif z < -5: z = -5
#         return z
#     weather_df = forecast_plot[['yhat']].pct_change()[-forecast_days_ahead:-(forecast_days_ahead - 10)].dot([1000]).astype(int).apply(correct_max_outliers)
#     return weather_df

In [18]:
# def correct_max_outliers (z):     
#     if z > 5: z = 5
#     elif z < -5: z = -5
#     return z
    
# this_list = pd.Series([6, 5, 3, 0, 100, -100, -5, -3, -2])
# # this_lamb(this_list)

# this_list.map(this_lamb)

In [19]:
# weather_emoticons(1)

In [20]:
# weather_emoticons(2)

In [21]:
# weather_emoticons(3)

In [22]:
# weather_emoticons(4)

In [23]:
# weather_emoticons(5)

In [24]:
# weather_emoticons(6)

In [25]:
# start_time = time.time()
# today = datetime.today()
# start_date = today - timedelta(weeks=weeeks_prior_data_end_date)
# start_date = start_date.replace(second=0, microsecond=0)

# data = yf.download('AAPL', start=start_date)

In [26]:
# data.columns

## Sentiment Analysis API Exploratory Analysis

In [94]:
# import requests
# import json
# from dotenv import load_dotenv
# import os

# load_dotenv()
# ma_key = os.getenv("MARKETAUX_TOKEN")
# ma_key1 = os.getenv("MARKETAUX_TOKEN2")
# ma_key2 = os.getenv("MARKETAUX_TOKEN3")
# ma_key3 = os.getenv("MARKETAUX_TOKEN4")
# ma_key4 = os.getenv("MARKETAUX_TOKEN5")

In [95]:

# first_key = [(ma_key, i) for i in adj_close_df.columns[:100]]
# second_key = [(ma_key1, j) for j in adj_close_df.columns[200:300]]
# third_key = [(ma_key2, k) for k in adj_close_df.columns[200:300]]
# fourth_key = [(ma_key3, l) for l in adj_close_df.columns[200:300]]
# fifth_key = [(ma_key4, m) for m in adj_close_df.columns[200:300]]

# # first_key = adj_close_df.columns[:100]
# # second_key = adj_close_df.columns[100:200]
# # third_key = adj_close_df.columns[200:300]
# # fourth_key = adj_close_df.columns[300:400]
# # fifth_key = adj_close_df.columns[400:]

In [96]:
# for i in second_key:
#     first_key.append(i)
# for i in third_key:
#     first_key.append(i)
# for i in fourth_key:
#     first_key.append(i)
# for i in fifth_key:
#     first_key.append(i)
    
# # first_key

In [117]:
# first_key = [(ma_key, i) for i in adj_close_df.columns[:100]]
# second_key = [(ma_key1, j) for j in adj_close_df.columns[200:300]]
# third_key = [(ma_key2, k) for k in adj_close_df.columns[200:300]]
# fourth_key = [(ma_key3, l) for l in adj_close_df.columns[200:300]]
# fifth_key = [(ma_key4, m) for m in adj_close_df.columns[200:300]]

# for i in second_key:
#     first_key.append(i)
# for i in third_key:
#     first_key.append(i)
# for i in fourth_key:
#     first_key.append(i)
# for i in fifth_key:
#     first_key.append(i)

# def calc_mean_score(ma_key_value, ticker_name_sym):
#     """
#     Accepts marketaux api key:
#       https://www.marketaux.com/documentation
#     Also accepts a ticker symbol.
    
#     Returns tickers mean sentiment score for time nearest calling the func.
#     """
#     ma_url = f'https://api.marketaux.com/v1/news/all?symbols={ticker_name_sym}&filter_entities=true&group_similar=false&language=en&api_token={ma_key_value}'
#     setntiment_data = requests.get(ma_url).json()
    
#     mean_score = 0
#     for i in range(len(setntiment_data['data'])):
#         mean_score += setntiment_data['data'][i]['entities'][0]['sentiment_score']

#     mean_score /= len(setntiment_data['data'])
    
#     return mean_score
#     # return ticker_name_sym, mean_score
    
# sentiment_series = pd.Series()
# empty_sentiment_series = pd.Series('NULL')

# for n in first_key[498:]:
#     try: sentiment_series = pd.concat([sentiment_series, pd.Series(calc_mean_score(n[0], n[1]))])
#     except: sentiment_series.concat([sentiment_series, empty_sentiment_series])


    


In [118]:


# sentiment_series = pd.Series()
# empty_sentiment_series = pd.Series('NULL')

# for n in first_key[498:]:
#     try: sentiment_series = pd.concat([sentiment_series, pd.Series(calc_mean_score(n[0], n[1]))])
#     except: sentiment_series.concat([sentiment_series, empty_sentiment_series])
#     # print(n)

# sentiment_series





0    0.355446
0    0.094250
dtype: float64

In [119]:
# for n in sentiment_series:
#     print(n)

0.3554456666666667
0.09425


In [102]:
# sentiment_list = []
# for n in first_key[498:]:
#     try: sentiment_list.append(calc_mean_score(n[0], n[1]))
#     except: sentiment_list.append(n[0], 'NULL')
#     # print(n)
# sentiment_list

[('MKC', 0.3554456666666667), ('MKTX', 0.09425)]

In [122]:
# sentiment_series#.dot([1000])

0    0.355446
0    0.094250
dtype: float64

In [ ]:
# weather_df = forecast_plot[['yhat']].pct_change()[-forecast_days_ahead:-(forecast_days_ahead - 10)].dot([1000]).astype(int).apply(correct_max_outliers)


In [103]:
# sentiment_list = []
# for n in first_key[300:310]:
#     try: sentiment_list.append(calc_mean_score(n[0], n[1]))
#     except: sentiment_list.append(n[0], 'NULL')
#     # print(n)
# sentiment_list

[('GL', 0.3686),
 ('GLW', 0.16005),
 ('GM', 0.255394),
 ('GNRC', -0.015224999999999983),
 ('GOOG', 0.35026666666666667),
 ('GOOGL', 0.33325466666666664),
 ('GPC', 0.25597766666666666),
 ('GPN', 0.45538733333333337),
 ('GRMN', 0.26655533333333337),
 ('GS', 0.03872533333333333)]

In [105]:
# sentiment_list[3][1]

-0.015224999999999983

In [ ]:
# start_time2 = time.time()

# p = Pool(cpu_count())
# p.starmap(calc_mean_score, first_key)
# p.close()
# p.join()
# print("--- %s seconds ---" % (time.time() - start_time2))

In [55]:
# ma_url = f'https://api.marketaux.com/v1/news/all?symbols={TICKER_NAME}&filter_entities=true&group_similar=false&language=en&api_token={ma_key}'

# setntiment_data = requests.get(ma_url).json()
# len(setntiment_data['data'])

In [54]:
# len(setntiment_data['data'])

In [47]:
# Extract Sentiment Scores
# setntiment_data['data'][0]['entities'][0]['sentiment_score'], setntiment_data['data'][1]['entities'][0]['sentiment_score'], setntiment_data['data'][2]['entities'][0]['sentiment_score']

(0.2233, 0.322636, 0.295967)

In [60]:
# score = calc_mean_score(TICKER_NAME, ma_key)
# score

0.11454533333333332